In [60]:
from pathlib import Path
import re

In [61]:
def normalise_dash(text):
    dashs = [
        "-",
        "֊",
        "־",
        "᐀",
        "᠆",
        "﹘",
        "゠",
        "〰",
        "〜",
        "⹀",
        "⸻",
        "⸺",
        "⸚",
        "⸗",
        "―",
        "—",
        "–",
        "‒",
        "‐",
        "‑",
        "－",
        "﹣",
        "=",
        "_",
    ]
    for dash in dashs:
        text = text.replace(dash, "-")
    text = re.sub("-+", "-", text)
    return text

In [62]:
def fix_abnormal_pagination(text, vol_num):
    if str(vol_num)[0] == "1":
        text = re.sub("\n7", "\n1", text)
    text = re.sub(f"{vol_num}ཝ་", f"{vol_num}-", text)
    text = re.sub(f"{vol_num}-.*?\n*([0-9]+)", rf"{vol_num}-\1", text)
    ab_pg_without_vol_nums = re.finditer(r"\n-([0-9]+)", text)
    for ab_pg_without_vol_num in ab_pg_without_vol_nums:
        pg_no = ab_pg_without_vol_num.group(1)
        text = re.sub(ab_pg_without_vol_num[0], f"\n{vol_num}-{pg_no}", text)
    ab_pgs = re.finditer(f"{vol_num}\n([0-9]+)\n\n", text)
    for ab_pg in ab_pgs:
        pg_no = ab_pg.group(1)
        text = re.sub(ab_pg[0], f"{vol_num}-{pg_no}\n\n", text)
    return text

In [63]:
def bind_pages(pages):
    return "".join(pages)

In [64]:
def get_pages(vol_text):
    result = []
    pg_text = ""
    pages = re.split(f"(\[\d+[a-b]\])", vol_text)
    for i, page in enumerate(pages[1:]):
        if i % 2 == 0:
            pg_text += page
        else:
            pg_text += page
            result.append(pg_text)
            pg_text = ""
    return result

In [65]:
def namsel_ab_page_fix(text, vol_num):
    ab_pgs = re.finditer(f"\n+({vol_num}\u0020*-*—*_*–*=*[0-9]+)", text)
    for ab_pg in ab_pgs:
        pg_ann = ab_pg.group(1)
        text = re.sub(ab_pg[0], f"\n{pg_ann}", text)
    return text

In [73]:
def normalise_pagination(page, vol_num):
    pg_ann = re.search(f"{vol_num}[\s\n]?(-|ཝ་|་|།|།དེ|\n)?[\s\n]?(([0-9][\s\n]?)+)", page)
    print(pg_ann[0])
    pg_no_part = pg_ann.group(2)
    pg_no = re.sub("\s|\n", "", pg_no_part)
    page = re.sub(pg_ann[0], f"{vol_num}-{pg_no}\n\n", page)
    return page

In [74]:
def find_next(prev_pg, cur_pg):
    prev_lines = prev_pg.splitlines()
    cur_pg_lines = cur_pg.splitlines()
    prev_pg_pat = re.search("\[(\d+)([a-z]{1})\]", prev_lines[0])
    prev_pg_num = int(prev_pg_pat.group(1))
    prev_pg_face = prev_pg_pat.group(2)
    cur_pg_pat = re.search("\[(\d+)([a-z]{1})\]", cur_pg_lines[0])
    cur_pg_num = int(cur_pg_pat.group(1))
    cur_pg_face = cur_pg_pat.group(2)
    if prev_pg_num == cur_pg_num - 1:
        if prev_pg_face == "b" and cur_pg_face == "a":
            return []
        elif prev_pg_face == "a" and cur_pg_face == "a":
            return [f"[{prev_pg_num}b]\n\n\n\n"]
        elif prev_pg_face == "b" and cur_pg_face == "b":
            return [f"[{cur_pg_num}a]\n\n\n\n"]
        elif prev_pg_face == "a" and cur_pg_face == "b":
            return [f"[{prev_pg_num}b]\n\n\n\n", f"[{cur_pg_num}a]\n\n\n\n"]
    elif prev_pg_num < cur_pg_num:
        next_pages = []
        for pg_num in range(prev_pg_num, cur_pg_num + 1):
            next_pages.append(f"[{pg_num}a]\n\n\n\n")
            next_pages.append(f"[{pg_num}b]\n\n\n\n")
        if prev_pg_face == "a" and cur_pg_face == "a":
            return next_pages[1:-2]
        elif prev_pg_face == "a" and cur_pg_face == "b":
            return next_pages[1:-1]
        elif prev_pg_face == "b" and cur_pg_face == "a":
            return next_pages[2:-2]
        elif prev_pg_face == "b" and cur_pg_face == "b":
            return next_pages[2:-1]
    else:
        return []

In [75]:
def reconstruct_pages(pages, vol_num):
    result = []
    for pg_walker, pg in enumerate(pages):
        pg = pg.replace("O", "0")
        cur_pg_lines = pg.splitlines()
        cur_pg_body = "\n".join(cur_pg_lines[1:])
        if re.search(f"{vol_num}[\s\n]?(-|ཝ་|་|།|\n)?[\s\n]?([0-9][\s\n]?)+", cur_pg_body):
            normalised_pg_body = normalise_pagination(cur_pg_body, vol_num)
            normalised_pg_body = normalised_pg_body.replace('\n','')
            pg = cur_pg_lines[0] + "\n" + normalised_pg_body
        if pg_walker == 0:
            if re.search("1a", cur_pg_lines[0]):
                result.append(pg)
            else:
                result.append("[1a]\n\n\n\n")
                next_pgs = find_next(result[-1], pg)
                if next_pgs:
                    for next_pg in next_pgs:
                        result.append(next_pg)
                result.append(pg)

        else:
            prev_pg = result[-1]
            next_pgs = find_next(prev_pg, pg)
            if next_pgs:
                for next_pg in next_pgs:
                    result.append(next_pg)
                result.append(pg)
            else:
                result.append(pg)
    return result

In [76]:
if __name__ == "__main__":
    potis = Path("../../v112.txt")
    potis.sort()
    print(len(potis))
    for vol_num, poti in enumerate(potis, 1):
        vol_text = poti.read_text(encoding="utf-8")
        vol_text = vol_text.replace("O", "0")
        vol_text = normalise_dash(vol_text)
        vol_text = fix_abnormal_pagination(vol_text, vol_num)
        vol_text = namsel_ab_page_fix(vol_text, vol_num)
        pages = get_pages(vol_text)
        new_pages = reconstruct_pages(pages, vol_num)
        new_vol_text = bind_pages(new_pages)
        Path(f"../tengyur_namsel/tengyur_namsel_reconstructed/v{vol_num:03}").write_text(
            new_vol_text, encoding="utf-8"
        )
        print(f"v{vol_num:03} completed...")

119
10

11

11
13

14

15

16

18

19

1-1
1-3

1-4

1-5

1-6

1-7

13
1-9

1-10

1-11

1-13

1-14

1-15

1-16

1-17

1-18

1-19

1-20

1-21

1-22

1-23

1-24

1-25

1-26

1-27

1-28

1-29

1-30

1-31

1-32

1-35

1-36

1-37

1-38

1-39

1-40

1-42

1-43

1-44

1-45

1-47

1-48

1-49

1-0

1-51

1-52

1-53

1-54

1-56

1-37

1-8

1-59

1-61

1-62

1-63

1-64

1-6
1-66

1-67

1-68

1-69

1-70

1-71

1-72

1-73

1-74

1-75

1-76

1-77

1-78

1-79

1-81

1-83

1-85

1-86

1-87

1-88

1-89

1-90

1-92

1-93

1-94

1-95

1-96

1-97

1-98

1-99

1-100

1-101

1-102

1-103

1-104

1-112

1-113

1-114

1-115

1-116

1-117

1-118

1-119

1-120

1-121

1-122

1-123

1-124

1།དེ125

1-126

1-127

1-128

1-129

1-130
1-131

1-132

1-133

1-134

1-135

1-136

1-137

1-138

1-139

1-140

1-141

1-142

1-143

1།དེ144

1།དེ145

1།དེ146

1-147

1།དེ148

1།དེ149

1-150

1-151

1-152

1།དེ153

1-154

1-155

1-156

1-157

1།དེ158

1-159

1-160

1-164

1-166

1-167

1-168

1-169

1-170

1-171

1-173

1-174


2-86

2-87

2-88

2-89

2-90

2-91

2-92

2-93

2-94

2-95

2-96

2-97

2-98

2-99

2-100

2-103

2-104

2-105

2-106

2-107

2-108

2-111

2-112

2-113

2-114

2-115

2-116

2-117

2-118

2-119

2-120

2-121

2-122

2-123

2-124

2-125

2-126

2-127

2-128

2-129

2-130

2-131

2-132

2-133

2-134

2-135

2-136

2-137

2-138

2-139

2-140

2-141

2-154

2-155

2-157

2-158

2-161

2-162

2-163

2-164

2-165

2-166

2-167

2-168

2-169

2-170

2-171

2-172

2-173

2-174

2-175

2-177

2-178

2-179

2-180

2-181

2-182

2-183

2-184

2-185

2-186

2-187

2-189

2-190

2-191

2-193

2-194

2-195

2-196

2-197

2-198

2-199

2-200

2-201

2-202

2-203

2-204

2-205

2-206

2-207

2-208

2-209

2-210

2-211

2-212

2-213

2-214

2།དེ215

2-216

2-217

2-218

2-219

2-220

2-221

2-222

2-223

2-224

2-225

2-226

2-227

2-228

2-229

2-230

2-231

2-232

2-233

2-234

2-235

2-236

2-237

2-238

2-239

2-240

2-241

2-242

2-243

2-244

2-245

2-246

2-247

2-248

2-249

2-250

2-251

2-2


3-378

3-379

3-380 
3-381

3-382

3-383

3-384

3-385

3-386

3-387
3-388

3-389

3-390

3-391

3-392

3-393

3-394

3-395

3-396

3-397

3-398

3-399

3-400

3-401

3-402

3-403

3-404

3-405

3-406

3-407

3-408

3-409

3-410

3-411

3-412

3-413

3-414

3-415

3-416

3-417

3-418

3-419

3-420

3-421

3-422

3-423

3-424

3-425

3-426

3-427

3-428

3-429

3-430

3-431

3-432

3-433

3-434

3-435

3-436

3-437

3-438

3-439

3-440

3-441

3-442

3-443

3-444

3-445

3-446

3-447

3-448

3-449

3-450

3-451

3-452

3-453

3-454

3-455

3-456

3-457

3-458

3-459

3-460

3-461

3-462

3-63

3-64

3-465

3-466

3-467

3-468 
3-469

3-70

3-471

3-472

3-473

3-474

3-475

3-476

3-477

3-478

3-479

3-480

3-481

3-482

3-483

3-484

3-485

3-486

3-487

3-488

3-489

3-490

3-491

3-492

3-493

3-494

3-19
3-496

3-497

3-198

3-99

3-500

3-501

3-02

3-503

3-504 
3-505

3-506

3-507

3-508

3-509

3-510

3-511

3-512

3-513

3-514

3-515

3-516

3-517

3-18

3-19

3-20

3-521

3-


4-390

4-391

4-392

4-393

4-394

4-395

4-396

4-397

4-398

4-399

4-400

4-401

4-402

4-403

4-404

4-405

4-406

4-7107

4-408

4-09

4-410

4-411

4-412

4-413

4-414

4-11
4-416

417

4-418

4-419

4-420

4-421

4-422

4-423

4-424

4-425

4-426

4-427

4-428

4-429

4-430

4-431

4-432

4-7133

4-434

4-435

4-436

4-437

4-438

4-439

4-440

4-441

4-442

4-443

4།དེ444

4-445

4-446

447

4-448

4-449

4-450

4-451

4-452

4-453

4-454

4-455

4-456

4-457

4-458

4-459

4-460

4-461

4-462

4-463

464

4-465

4-466

4-467

4-468

4-469

4-470

4-471

4-172

4-473

4-474

4-475

4-476

4-477

4-178

4-479

4-480

4-481

4-482

4-483

4-484

4-485

4-486

4-487

4-488

4-489

4-490

4-491

4-492

4-493

4-494

4-495

4-496

4-497

4-498

4-499

4-500

4-501

4-503

4-50
4-506

4-507

4-008

4-509

4-510

4-511

4-12

4-513

4-514

4-515

4-17

4-19

4-521

4-522

4-523

4-524

4-535

4-527

4-529

4-30

4-531

4-33

4-3
4-35

4-537

4-539

4-540

4-541

4-2

4-43

4-545

4-6


5-307

5-308

5-309

5-310

5-311

5-312

5-313

5-314

5-315

5-316

5-317

5-318

5-319

5-320

5-321

5-322

5-323

5-324

5-325

5-326

5-327

5-328

5-329

5-330

5-331

5-332

5-333

5-334

5-335

5-336

5-337

5-338

5-339

5-340

5-341

5-342

5-343

5-349

5-350

5-351

5-352

5-353

5-354

5-355

5-356

5-359

5-360

5-361

5-362

5-363

5-364

5-365

5-366

5-367

5-368

5-369

5-370

5-371

5-372

5-373

5-374

5-375

5-376

5-377

5-378

5-379

5-380

5-381

5-382

5-383

5-384

5-385

5-386

5-387

5-388

5-389

5-390

5-391

5-392

5-393

5-394

5-395

5-396

5-397

5-398

5-399

5-400

5-401

5-402

5-403

5-404

5-405

5-406

5-407

5-408

5-409

5-410

5-411

5-412

5-413

5-414

5-415

5-416

5-417

5-418

5-422

5-423

5-424

5-425

5-426

5-427

5-428

5-429

5-430

5-431

5-432

5-433

5-434

5-435

5-436

5-437

5-438

5-439

5-440

5-441

5-442

5-443

5-445

5-446

5-447

5-448

5-449

5-450

5-451

5-452

5-453

5-454

5-455

56

5-457

5-458

5-459

5-460

5

...

107-3

107-4

107-5

107-6

107-7

107-8

107-9

107-10

107-11

107-12

107-13

107-14

107-15

107-16

107-17

107-18

107-19

107-20

107-21

107-22

107-23

107-24

107-25

107-26

107-27

107-28

107-29

107-32

107-33

107-34

107-35

107-38

107-39

107-40

107-41

107-42

107-44

107-45

107-46

107-47

107-48

107-49

107-50

107-52

107-53

107-54

107-55

107-56

107-58

107-59

107-60

107-61

107-62

107-63

107-65

107-66

107-67

107-68

107-69

107-70

107-71

107-73

107-74

107-75

107-76

107-77

107-78

107-79

107-80

107-81

107-82

107-83

107-84

107-85

107-86

107-87

107-88

107-89

107-90

107-91

107-92

107-93

107-94

107-95

107-96

107-97

107-98

107-99

107-100

107-101

107-102

107-103

107-104

107-105

107-106

107-107

107-108

107-109

107-110

107-111

107-112

107-113

107-114

107-115

107-116

107-117

107-118

107-119

107-120

107-121

107-122

107-123

107-124

107-125

107-126

107-127

107-128

107-129

107-130

107-131

107-132

107-13


107-1136

107-1137

107-1138

107-1139

107-1140

107-1141

107-1142

107-1143

107-1144

107-1145

107-1146

107-1147

107-1148

107-1149

107-1150

107-1151

107-1152

107-1153

107-1154

107-1155

107-1156

107-1157

107-1158

107-1159

107-1160

107-1161

107-1162

107-1163

107-1164

107-1165

107-1166

107-1167

107-1168

107-1169

107-1170

107-1171

107-1172

107-1173

107-1174

107-1175

107-1176

107-1177

107-1178

107-1179

107-1180

107-1181

107-1182

107-1183

107-1184

107-1185

107-1186

107-1187

107-1188

107-1189

107-1190

107-1191

107-1192

107-1193

107-1194

107-1195

107-1196

107-1197

107-1198

107-1199

107-1200

107-1201

107-1202

107-1203

107-1204

107-1205

107-1206

107-1207

107-1208

107-1209

107-1210

107-1211

107-1212

107-1213

107-1214

107-1215

107-1216

107-1217

107-1218

107-1219

107-1220

107-1221

107-1222

107-1223

107-1224

107-1225

107-1226

107-1227

107-1228

107-1229

107-1230

107-1231

107-1232

107-1233

107-1234

107-1235



108 -1506

108-1508

108-1510

108-1515

108-1518

108-1519

108-1523

108-1525

108-1527

108-1528

108-1529

108-1530

108-533

108-1536

108-1537

108-1538

108-1540

108-1547

108 ་549

108 1551

108-1553

108-556

108-1561

108-1565

108-1570

108-1573

108-1574

108-1576

108-1579

108-1581

108-1587

108-1588

108-1589

108-1590

108-1593

108-1596

108-1597

108-1599

108-1605

108-1606

108-1607

108-1609

108-1610

108-1611

108-1612

108-1613

108-1616

108-1617

108-1620

108-1621

108-1624

108-1625

108-1627

108-1628

108-1629

108-1630

108-1631

108-1633

108-1635

108-1636

108-1637

108-1638

108-1639

108-1640

108-1641

108-1642

108-1644

108 1645

108-1646

108-1647

108-1648

108-1649

108-1650

108-1651

108-1652

108-1653

108-1654

108-1656

108-1657

108-1658

108-1660

108-1661

108-1662

108-1664

108-1665

108-1666

108-1667

108-1668

108-1669

108-1670

108-1671

108-1672

108-1673

108-1674

108-1675

108-1676

108-1677

108-1678

108-1680

108-1681




110-245

110-246

110-247

110-252

110-256

110-257

110-260

110-263

110-264

110-271

110-273

110-274

110-278

110-280

110-283

110-285

110-286

110-293

110-295

110-298

110-299

110-303

110-307

110-311

110-313

110-314

110-317

110-321

110-323

110 324

110-326

110-327

110-329

110-330

110-331

110-333

110-334

110-335

110-338

110-347

110-351

110-353

110-354

110-355

110-356

110-357

110-358

110-359

110-360

110-361

110-362

110-363

110-364

110-365

110-366

110-367

110-368

110-369

110-370

110-371

110-375

110-376

110-377

110-378

110-379

110-380

110-383

110-387

110-389

110-390

110-391

110-393

110-394

110-396

110-398

110-399

110-402

110-421

110-423

110-424

110-425

110-426

110-429

110-430

110-431

110-433

110-436

110-438

110-439

110-443

110-446

110-452

110-453

110-456

110-459

110-463

110-470

110-473

110-478

110-479

110-481

110-482

110-484

110-486

110-490

110-492

110-495

110-497

110-498

110-502

110-503



v111 completed...
1120

1121

1122

1123

1124

1125

1126

1127

1128

1129

v112 completed...
1132

1138

v113 completed...
1140

1141

1142

1143

1144

1145

1146

1147

1148

1149

v114 completed...
1150

1151

1152

1153

1154

1155

1156

1157

1158

1159

v115 completed...
1162

1164

1166

1167

1169

v116 completed...
v117 completed...
v118 completed...
1190

1191

1193

1194

1195

1196

1197

1198

1199

1193

v119 completed...
